# Processing CSV files

In [1]:
import pandas as pd
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import data_processing as dp

pd.options.display.float_format = '{:.4f}'.format

IMU_list = ['BMI270', 'BMI055', 'ICM42688', 'MPU6000', 'PIXHAWK6c']

datasets = ['ATT', 'IMU']

# Adding fast sensor readings 
datasets += ['RGY2', 'RAC2']

df_dict = dp.load_suspend_data_pixhawk_invensense(datasets,imu=IMU_list[4])

df_transition = dp.compute_transition_df(source_df=df_dict['GT2'], param='Ground_Truth')

print("[**] transition dataframe")
print(df_transition)


[**] transition dataframe
       timestamp  Ground_Truth  transition
5779    153.0404           100    100.0000
8279    154.2908             0   -100.0000
15779   158.3396           100    100.0000
18279   159.5919             0   -100.0000
25779   163.6555           100    100.0000
28279   164.9058             0   -100.0000
35779   168.9684           100    100.0000
38279   170.2207             0   -100.0000
45779   174.2811           100    100.0000
48279   175.5314             0   -100.0000
55779   179.6042           100    100.0000
58279   180.8545             0   -100.0000
65779   184.9275           100    100.0000
68279   186.1779             0   -100.0000


## Enriching Datasets

In [2]:
df=df_dict['GT2']
param='Ground_Truth'
stats_params = {  
            'IMU': 
                ['GyrX', 'GyrY', 'GyrZ', 'AccX', 'AccY', 'AccZ'],
            'RAC2':
                ['ACCx'],#'ACCy','ACCz'],
            'RGY2':
                ['GYROx'],#'GYROy','GYROz'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw']
        }


# Add attack column into based on timestamps from the transition dataframe
for k in stats_params.keys():
    attack0 = df[param].iloc[0]
    attack = list()
    this_df = df_dict[k]
    tr0 = 0
    for tr in df_transition['timestamp'].values:
        data_size = len(this_df[(this_df['timestamp']>tr0) & (this_df['timestamp']<=tr)])
        # print('adding {} data points to {} points'.format(data_size, len(attack)))
        attack += [attack0]*data_size
        attack0 = df_transition['Ground_Truth'][df_transition['timestamp']==tr].values[0]
        tr0 = tr
    # Compute last segment
    data_size = len(this_df[this_df['timestamp']>tr])
    # print('adding {} data points to {} points'.format(data_size, len(attack)))
    attack += [attack0]*data_size
    this_df['attack'] = attack
    
    # Add 'update' column with the time diference between data points
    this_df['update'] = this_df['timestamp'].diff()

    df_dict[k] = this_df

update_dict = dict()
for ds in datasets[:-1]:
    df_update = pd.DataFrame()
    df_update['timestamp'] = df_dict[ds]['timestamp']
    df_update['update'] = df_dict[ds]['timestamp'].diff()
    update_dict[ds] = df_update
    

# Statistical Results

In [3]:

stat_dict = dict()
param_set = list()

for k,values in stats_params.items():
    for v in values+['update']:
        this_df = df_dict[k]
        # tr0 = 0
        # compute mean and std deviation for all variables in 'stats_params'
        atk_set = this_df['attack'].unique()
        for atk in atk_set:
            if 'update' in v:
                filtered_list = 1/this_df[v][this_df['attack']==atk]
            else:
                filtered_list = this_df[v][this_df['attack']==atk]

            mean_value = filtered_list.mean()
            std_value = filtered_list.std()

            # fill up the stat_dict dictionary by attack
            name_code = '{}.{}'.format(k, v)
            param_set.append(name_code)
            if atk in stat_dict:
                    stat_dict[atk][name_code] = {'mean': mean_value, 'std':std_value}
            else:
                stat_dict[atk] = {name_code:{'mean': mean_value, 'std':std_value}}

# convert stats into a dataframe
df_columns = ['Freq']
for i in list(set(param_set)):
    df_columns+= [i+'.mean', i+'.std']
stat_df = pd.DataFrame(columns=df_columns)
stat_df['Freq'] = atk_set
for freq in stat_dict:
    for param in stat_dict[freq]:
        stat_df.loc[stat_df['Freq']==freq,param+'.mean'] = stat_dict[freq][param]['mean']
        stat_df.loc[stat_df['Freq']==freq,param+'.std'] = stat_dict[freq][param]['std']

pd.options.display.float_format = '{:.4f}'.format
print(stat_df.loc[stat_df['Freq']!=0])
print(stat_df[['IMU.AccX.mean', 'IMU.AccX.std',
               'IMU.AccY.mean', 'IMU.AccY.std',
               'IMU.AccZ.mean', 'IMU.AccZ.std',
               'IMU.GyrX.mean', 'IMU.GyrX.std',
               'IMU.GyrY.mean', 'IMU.GyrY.std',
               'IMU.GyrZ.mean', 'IMU.GyrZ.std',]].loc[stat_df['Freq']!=0].to_latex())

   Freq IMU.AccY.mean IMU.AccY.std IMU.GyrZ.mean IMU.GyrZ.std ATT.Roll.mean  \
1   100       -0.1496       0.0089        0.0005       0.0008        0.1525   

  ATT.Roll.std RAC2.ACCx.mean RAC2.ACCx.std RGY2.update.mean  ...  \
1       0.1239        -0.1185        0.0061        6949.8567  ...   

  IMU.GyrY.mean IMU.GyrY.std IMU.update.mean IMU.update.std ATT.update.mean  \
1       -0.0010       0.0024        408.0761        81.9777        409.4284   

  ATT.update.std IMU.AccX.mean IMU.AccX.std IMU.GyrX.mean IMU.GyrX.std  
1        86.0203       -0.4904       0.0084        0.0004       0.0027  

[1 rows x 31 columns]
\begin{tabular}{lllllllllllll}
\toprule
 & IMU.AccX.mean & IMU.AccX.std & IMU.AccY.mean & IMU.AccY.std & IMU.AccZ.mean & IMU.AccZ.std & IMU.GyrX.mean & IMU.GyrX.std & IMU.GyrY.mean & IMU.GyrY.std & IMU.GyrZ.mean & IMU.GyrZ.std \\
\midrule
1 & -0.490412 & 0.008388 & -0.149551 & 0.008892 & -9.955914 & 0.010847 & 0.000381 & 0.002691 & -0.001040 & 0.002414 & 0.000453 & 0.0008

## Plotting Suspend attack results

In [ ]:
import plot_formatting as pfg

fig = make_subplots(rows=4, cols=1,
                    shared_xaxes=True,
                    vertical_spacing = 0.02,
                    row_heights=[.25]*2 + [.25]*2)

colorset = px.colors.qualitative.Bold

# Plot data source
plot_params = {  
            #'IMU': 
            #    ['GyrX', 'AccX'],
            'RAC2':
                ['ACCx', 'update'],
            'RGY2':
                ['GYROx', 'update'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw', 'update'],
        }


plot_labels = {
                'RAC2':'Accel', 
               'RGY2': 'Gyro',
               'ATT': 'EKF Estimation'}

x_range = [179, 180] #[94.3, 94.7]

color_ix = 0
for k,values in plot_params.items():
    for v in values:
        row_num  = 1
        this_df = df_dict[k]
        this_df = this_df.loc[(this_df['timestamp']>x_range[0]) & (this_df['timestamp']<x_range[1])]
        if 'G' in v:
            row_num = 2
        tr0 = 0
        # Plotting attitude
        if 'ATT' in k and not ('update' in v):
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                    name= v,
                    mode='lines',
                    legendgroup=k,
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=3,
                    legendgrouptitle_text='Attitude'),
                row=3,col=1)
        # PLotting update frequencies
        elif 'update' in v:
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=1/this_df[v],
                    name= plot_labels[k],
                    mode='lines',
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=5,
                    legendgroup='freq',
                    legendgrouptitle_text='Frequency'),
                row=4,col=1)
        else:
            # Plotting Accelerometer and Gyro
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                    name= k+str('.')+v,
                    mode='lines',
                    legendgroup=v,
                    line=dict(color=colorset[color_ix]),
                    showlegend=False),
                row=row_num,col=1)

        color_ix += 1


# Plot attacks
df = df_dict['GT2']
df = df.loc[(df['timestamp']>x_range[0]) & (df['timestamp']<x_range[1])]


# inlcude attack transitions as vertical lines in the figure 
for v in df_transition['timestamp'][(df_transition['timestamp']>x_range[0]) & (df_transition['timestamp']<x_range[1])].values:
    fig.add_vline(x=v)

# beautify plots
fig = pfg.beautify_plot(fig)

subplot_titles=['value', 'data rate', 'freq'],
layout = go.Layout( autosize=True, margin={'l': 0, 'r': 0, 't': 0, 'b': 0})
fig['layout'].update(layout)

#  Formating x-axis
fig['layout']['xaxis'].update(range=x_range)
fig['layout']['xaxis4'].update(title='Time [s]', mirror=True)

# Formating y-axis
fig['layout']['yaxis1'].update(title='Accel X [m/s/s]')
fig['layout']['yaxis2'].update(title='Gyro X [rad/s]', tickvals = [-0.01, 0.00, 0.01, 0.02, 0.03])
fig['layout']['yaxis4'].update(title='Frequency [Hz]')
fig['layout']['yaxis3'].update(title='Attitude [°]')

fig['layout']['legend'].update(orientation='h',
                                x=0.2,
                                y=0.45,
                                   )

fig.show()
#Note use plotly 5.6.0, with more than 5.6.0 it might force the azis to rescale automatically to the last point where there aree data, which is not what we want


In [5]:
fig.write_image('figs/ICM42688Suspend.pdf')

## Plotting Frequency attack results

In [6]:
import data_processing as dp

IMU_list = ['BMI270', 'BMI055', 'ICM42688', 'MPU6000', 'PIXHAWK6c']

datasets = ['ATT', 'IMU']
# Adding fast sensor readings 
datasets += ['RGY2', 'RAC2']

df_dict = dp.load_frequency_data_pixhawk_invensense(datasets,imu=IMU_list[4])

df_transition = dp.compute_transition_df(source_df=df_dict['AC2'], param='Ground_Truth')
print("[**] transition dataframe")
print(df_transition)

[**] transition dataframe
        timestamp  Ground_Truth  transition
5214     127.2035      100.0000   -100.0000
15214    132.2285       50.0000    -50.0000
25214    137.2371       25.0000    -25.0000
35214    142.2489       12.5000    -12.5000
45214    147.2514     2000.0000   1987.5000
55214    152.6749     1000.0000  -1000.0000
65214    157.8764      200.0000   -800.0000
75214    162.9213      100.0000   -100.0000
85214    167.9385       50.0000    -50.0000
95214    172.9544       25.0000    -25.0000
105214   177.9586       12.5000    -12.5000
115214   182.9681     2000.0000   1987.5000
125214   188.3825     1000.0000  -1000.0000
135214   193.5749      200.0000   -800.0000


In [7]:
## Enriching Dataset

df=df_dict['AC2']
param='Ground_Truth'
stats_params = {  
            'IMU': 
                ['GyrX', 'GyrY', 'GyrZ', 'AccX', 'AccY', 'AccZ'],
            'RAC2':
                ['ACCx'],
            'RGY2':
                ['GYROx'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw']
        }


# Add attack column into based on timestamps from the transition dataframe
for k in stats_params.keys():
    attack0 = df[param].iloc[0]
    attack = list()
    this_df = df_dict[k]
    tr0 = 0
    for tr in df_transition['timestamp'].values:
        data_size = len(this_df[(this_df['timestamp']>tr0) & (this_df['timestamp']<=tr)])
        # print('adding {} data points to {} points'.format(data_size, len(attack)))
        attack += [attack0]*data_size
        attack0 = df_transition['Ground_Truth'][df_transition['timestamp']==tr].values[0]
        tr0 = tr
    # Compute last segment
    data_size = len(this_df[this_df['timestamp']>tr])
    # print('adding {} data points to {} points'.format(data_size, len(attack)))
    attack += [attack0]*data_size
    this_df['attack'] = attack
    
    # Add 'update' column with the time diference between data points
    this_df['update'] = this_df['timestamp'].diff()

    df_dict[k] = this_df

update_dict = dict()
for ds in datasets[:-1]:
    df_update = pd.DataFrame()
    df_update['timestamp'] = df_dict[ds]['timestamp']
    df_update['update'] = df_dict[ds]['timestamp'].diff()
    update_dict[ds] = df_update



## Statistical Result

stat_dict = dict()
param_set = list()

for k,values in stats_params.items():
    for v in values+['update']:
        this_df = df_dict[k]
        # tr0 = 0
        # compute mean and std deviation for all variables in 'stats_params'
        atk_set = this_df['attack'].unique()
        for atk in atk_set:
            if 'update' in v:
                filtered_list = 1/this_df[v][this_df['attack']==atk]
            else:
                filtered_list = this_df[v][this_df['attack']==atk]

            mean_value = filtered_list.mean()
            std_value = filtered_list.std()

            # fill up the stat_dict dictionary by attack
            name_code = '{}.{}'.format(k, v)
            param_set.append(name_code)
            if atk in stat_dict:
                    stat_dict[atk][name_code] = {'mean': mean_value, 'std':std_value}
            else:
                stat_dict[atk] = {name_code:{'mean': mean_value, 'std':std_value}}

# convert stats into a dataframe
df_columns = ['Freq']
for i in list(set(param_set)):
    df_columns+= [i+'.mean', i+'.std']
stat_df = pd.DataFrame(columns=df_columns)
stat_df['Freq'] = atk_set
for freq in stat_dict:
    for param in stat_dict[freq]:
        stat_df.loc[stat_df['Freq']==freq,param+'.mean'] = stat_dict[freq][param]['mean']
        stat_df.loc[stat_df['Freq']==freq,param+'.std'] = stat_dict[freq][param]['std']


print(stat_df.loc[stat_df['Freq']!=0])
print(stat_df.to_latex())

       Freq IMU.AccY.mean IMU.AccY.std IMU.GyrZ.mean IMU.GyrZ.std  \
0  200.0000       -0.1495       0.0036       -0.0288       0.3948   
1  100.0000       -0.1517       0.0024        0.0300       0.8625   
2   50.0000       -0.1530       0.0008        0.0327       0.4289   
3   25.0000       -0.1532       0.0000       -0.0556       0.5761   
4   12.5000       -0.1522       0.0080        0.0003       0.0049   
5 2000.0000       -0.1529       0.0082        0.0039       0.2520   
6 1000.0000       -0.1494       0.0066       -0.0180       0.3204   

  ATT.Roll.mean ATT.Roll.std RAC2.ACCx.mean RAC2.ACCx.std RGY2.update.mean  \
0       -4.2821       2.9406        -0.1147        0.0052         198.9687   
1       -0.6114       2.6291        -0.1146        0.0052          99.0508   
2       -0.0903       4.2277        -0.1145        0.0053          49.5458   
3        0.6132       3.0911        -0.1145        0.0052          24.9210   
4        0.9269       1.5932        -0.1135        0.0051

In [8]:
import plot_formatting as pfg

fig = make_subplots(rows=4, cols=1,
                    shared_xaxes=True,
                    vertical_spacing = 0.02,
                    row_heights=[.25]*2 + [.25]*2)

colorset = px.colors.qualitative.Vivid

# Plot data source
plot_params = {  
            'IMU': 
                ['GyrX', 'AccX', 'update'],
            'RAC2':
                ['ACCx', 'update'],
            'RGY2':
                ['GYROx', 'update'],
            'ATT':
                ['Roll', 'Pitch', 'Yaw', 'update'],
        }

# Legend labels
plot_labels = {'RAC2':'Accel', 
               'RGY2': 'Gyro',
               'ATT': 'EKF Estimation',
               'IMU': 'IMU'}

x_range = [157,192]

color_ix = 0
for k,values in plot_params.items():
    for v in values:
        row_num  = 1
        this_df = df_dict[k]
        this_df = this_df.loc[(this_df['timestamp']>x_range[0]) & (this_df['timestamp']<x_range[1])]
        if 'G' in v:
            row_num = 2

        tr0 = 0
        if 'ATT' in k and not ('update' in v):
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                    name= v,
                    mode='lines',
                    legendgroup=k,
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=3,
                    legendgrouptitle_text='Attitude'),
                row=3,col=1)
        # PLotting update frequencies
        elif 'update' in v:
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=1/this_df[v],
                    name= plot_labels[k],
                    mode='lines',
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    legendrank=5,
                    legendgroup='freq',
                    legendgrouptitle_text='Frequency',
                    opacity=0.5),
                row=4,col=1)
        else:
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
                    name= v,
                    mode='lines',
                    legendgroup=v,
                    line=dict(color=colorset[color_ix]),
                    showlegend=False),
                row=row_num,col=1)


        color_ix += 1

# Plot attacks
df = df.loc[(df['timestamp']>x_range[0]) & (df['timestamp']<x_range[1])]
# inlcude attack transitions as vertical lines in the figure 
for v in df_transition['timestamp'][(df_transition['timestamp']>x_range[0]) & (df_transition['timestamp']<x_range[1])].values:
    fig.add_vline(x=v)


# beautify plots
fig = pfg.beautify_plot(fig)

subplot_titles=['value', 'data rate', 'freq'],

#  Formating x-axis
fig['layout']['xaxis'].update(range=x_range)
fig['layout']['xaxis1'].update(side='top', mirror=True)
fig['layout']['xaxis2'].update(side='top', mirror=True)
fig['layout']['xaxis3'].update(mirror=True)
fig['layout']['xaxis4'].update(title='Time [s]', mirror=True)
# fig['layout'].update(yaxis_type="log", yaxis_range=[.0045,2])

# Formating y-axis
# fig['layout']['yaxis1'].update(range=[141.52,141.53], tickvals = [141.52, 141.53],)
fig['layout']['yaxis1'].update(title='Accel X [m/s/s]')
# fig['layout']['yaxis2'].update(range=[0.45,0.55])
# fig['layout']['yaxis3'].update(range=[31.47,31.5], tickvals = [31.47,31.5],)
fig['layout']['yaxis2'].update(title='Gyro X [rad/s]')
# fig['layout']['yaxis4'].update(range=[-0.015,0.015])
fig['layout']['yaxis4'].update(title='Frequency [Hz]')
fig['layout']['yaxis3'].update(title='Attitude [°]')
fig['layout']['yaxis4'].update(range=[0,4], type='log')

fig['layout']['legend'].update(orientation='h',
                                x=0.65,
                                y=0.45,
                                   )

fig.show()


In [9]:
# fig.write_image('figs/ICM42688Frequency.pdf')

In [10]:
import plot_formatting as pfg
import plotly.graph_objects as go
layout = go.Layout( autosize=True, margin={'l': 0, 'r': 0, 't': 0, 'b': 0})
fig = go.Figure(layout=layout)
fig2 = go.Figure()

colorset = px.colors.qualitative.Vivid

# Plot data source
plot_params = {  
            # 'IMU': 
            #     ['GyrX', 'AccX', 'update'],
            'RAC2':
                ['ACCx', 'update'],
            'RGY2':
                ['GYROx', 'update'],
            # 'ATT':
            #     ['Roll', 'Pitch', 'Yaw', 'update'],
        }

# Legend labels
plot_labels = {'RAC2':'Accel', 
               'RGY2': 'Gyro',
               'ATT': 'EKF Estimation',
               'IMU': 'Processed IMU'}

x_range = [150,182]

color_ix = 0
for k,values in plot_params.items():
    for v in values:
        row_num  = 1
        this_df = df_dict[k]
        this_df = this_df.loc[(this_df['timestamp']>x_range[0]) & (this_df['timestamp']<x_range[1])]
        if 'G' in v:
            row_num = 2

        tr0 = 0
        # if 'ATT' in k and not ('update' in v):
        #     fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
        #             name= v,
        #             mode='lines+markers',
        #             legendgroup=k,
        #             line=dict(color=colorset[color_ix]),
        #             showlegend=True,
        #             legendrank=3,
        #             legendgrouptitle_text='Attitude'),
        #         row=3,col=1)
        # PLotting update frequencies
        if 'update' in v:
            print(this_df)
            fig.add_trace(go.Scatter(x=this_df['timestamp'], y=1/this_df[v],
                    name= plot_labels[k],
                    mode='lines',
                    line=dict(color=colorset[color_ix]),
                    showlegend=True,
                    # legendrank=5,
                    # legendgroup='freq',
                    # legendgrouptitle_text='Frequency',
                    opacity=0.8))
            fig2.add_violin(x=this_df['attack'], y=1/this_df[v], name=plot_labels[k])
            color_ix += 1
        # else:
        #     fig.add_trace(go.Scatter(x=this_df['timestamp'], y=this_df[v],
        #             name= v,
        #             mode='lines+markers',
        #             legendgroup=v,
        #             line=dict(color=colorset[color_ix]),
        #             showlegend=False),
        #         row=row_num,col=1)


        

# Plot attacks
df = df.loc[(df['timestamp']>x_range[0]) & (df['timestamp']<x_range[1])]
# inlcude attack transitions as vertical lines in the figure 
for v in df_transition['timestamp'][(df_transition['timestamp']>x_range[0]) & (df_transition['timestamp']<x_range[1])].values:
    fig.add_vline(x=v)

fig = pfg.beautify_plot(fig)


fig['layout'].update(width=800, height=400,font_size=25)
fig['layout']['yaxis'].update(range=[1,4], type='log')

fig['layout']['xaxis'].update(title='Time [s]', mirror=True, range=x_range)
fig['layout']['yaxis'].update(title='Frequency [Hz]')
fig['layout']['legend'].update(orientation='h',
                                x=0.4,
                                y=1,
                                   )


# beautify plots
fig.show()

fig2 = pfg.beautify_plot(fig2)


fig2['layout'].update(width=1200, height=400)
fig2['layout']['yaxis'].update(range=[1,4], type='log')

fig2['layout']['xaxis'].update(title='Freq set [Hz]')
fig2['layout']['yaxis'].update(title='Frequency [Hz]', type='log')

fig['layout']['legend'].update(orientation='h',
                                x=0.4,
                                y=1,
                                   )
fig2.show()

       timestamp     TimeUS    ACCx    attack  update
6886    150.0001  150000138 -0.0958 2000.0000  0.0005
6887    150.0007  150000663 -0.1053 2000.0000  0.0005
6888    150.0014  150001404 -0.1101 2000.0000  0.0007
6889    150.0019  150001932 -0.1197 2000.0000  0.0005
6890    150.0025  150002456 -0.1245 2000.0000  0.0005
...          ...        ...     ...       ...     ...
19230   181.6290  181628954 -0.1197   12.5000  0.0810
19231   181.7100  181709987 -0.1053   12.5000  0.0810
19232   181.7910  181791010 -0.1197   12.5000  0.0810
19233   181.8720  181872032 -0.1101   12.5000  0.0810
19234   181.9526  181952573 -0.1245   12.5000  0.0805

[12349 rows x 5 columns]
       timestamp     TimeUS  GYROx    attack  update
6886    150.0001  150000144 0.0023 2000.0000  0.0005
6887    150.0007  150000670 0.0012 2000.0000  0.0005
6888    150.0014  150001411 0.0001 2000.0000  0.0007
6889    150.0019  150001939 0.0001 2000.0000  0.0005
6890    150.0025  150002462 0.0033 2000.0000  0.0005
...     

In [11]:
fig.write_image('figs/ICM42688Frequency.pdf')